Карта ОКН Саранска


## 1. Испортируем библиотеки


In [652]:
## Для работы с датасетами и геоданными

import pandas as pd
import geopandas as gpd
import folium

from shapely import geometry


## 2. Загружаем данные в формате geojson

In [653]:
data = gpd.read_file('./okn_all_pts.geojson') # Все ОКН
data_pts = gpd.read_file('./okn_pts.geojson') # ОКН, которые не являются зданиями (точки)
data_poly = gpd.read_file('./okn_ply.geojson') # Полигоны зданий
borders = gpd.read_file('./sar_border_lin.geojson') # Границы города

data_poly['Адрес'] = data_poly['Полный адрес'].str[33:] #Оставляем только улицу и номер дома
data_poly['Год постановки ОКН на Госохрану'] = data_poly['год постановки ОКН на Госохрану'].str.replace('NA', 'нет информации') #убираем NA
data_poly['Адрес'] = data_poly['Адрес'].str.replace('"""', '')

data_pts['Адрес'] = data_pts['Полный адрес'].str[33:] #Оставляем только улицу и номер дома
data_pts['Год постановки ОКН на Госохрану'] = data_pts['год постановки ОКН на Госохрану'].str.replace('NA', 'нет информации') #убираем NA
data_pts['Адрес'] = data_pts['Адрес'].str.replace('"""', '')

## 2. Создаем сетку (fishnet)

- карта плотности ОКН


#### 2.1. Перепроектируем данные (на всякий случай) для создания сетки

In [654]:
data = data.to_crs("EPSG:32641")

#### 2.2. Экстент данных


In [655]:
total_bounds = data.total_bounds
minX, minY, maxX, maxY = total_bounds

#### 2.3. Выбираем сторону квадрата сетки
- 300м – подходящее значение, так как ОКН в Саранске расположены достаточно компактно


In [656]:
square_size = 300

#### 2.4. Создаем fishnet

In [657]:
grid_cells = []
x, y = (minX, minY)
geom_array = []

while y <= maxY:
        while x <= maxX:
            geom = geometry.Polygon([(x,y), (x, y+square_size), (x+square_size, y+square_size), (x+square_size, y), (x, y)])
            geom_array.append(geom)
            x += square_size
        x = minX
        y += square_size


fishnet = gpd.GeoDataFrame(geom_array, columns=['geometry']).set_crs('EPSG:32641')
fishnet['id'] = fishnet.index

## 3. Считаем число ОКН в сетке


In [658]:
merged = gpd.sjoin(data, fishnet, how='left', predicate='within')
merged['n'] = 1
dissolve = merged.dissolve(by="id", aggfunc="count")
fishnet.loc[dissolve.index, 'n'] = dissolve.n.values

## 4. Создаем веб-карту


#### 4.1 Настройки карты



In [659]:
data = data.to_crs('EPSG:4326')
data_pts = data_pts.to_crs('EPSG:4326')

m = folium.Map(location=[data.centroid.y.mean(), data.centroid.x.mean()], zoom_start=12,  tiles="cartodb positron", control_scale=True)


/var/folders/s5/8q8ch8xx00v9lzkf9k7d3l3w0000gn/T/ipykernel_14581/3640412356.py:4: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  m = folium.Map(location=[data.centroid.y.mean(), data.centroid.x.mean()], zoom_start=12,  tiles="cartodb positron", control_scale=True)


#### 4.2 Добавляем слой с плотностью ОКН


In [660]:
folium.Choropleth(
    geo_data=fishnet,
    data=fishnet,
    columns=['id', 'n'],
    fill_color='YlGnBu',
    fill_opacity = 0.5,
    key_on='id',
    nan_fill_opacity=0,
   line_color = "#0000",
   legend_name="Количество объектов культурного наследия",
   name='Плотность ОКН',
   show=False
).add_to(m)

#### 4.3.1 Добавляем слой со зданиями


In [661]:


folium.GeoJson(
    data_poly,
    name="Здания ОКН",
    tooltip=folium.GeoJsonTooltip(fields=["Объект"]),
    popup=folium.GeoJsonPopup(fields=['Объект','дата создания', 'Адрес','Категория историко-культурного значения', 'Год постановки ОКН на Госохрану']),
    style_function=lambda x: {
        "fillColor": 'red',
        "color":"darkred"
    },
    highlight_function=lambda x: {"fillOpacity": 0.8},
    zoom_on_click=True,
    show=True,
).add_to(m)


#### 4.3.2 Добавляем слой с точечными ОКН
- оставим слой выключенным, т.к. за визуализацию точечных ОКН будет отвечать слой с кластеризацией, однако пользователь при желании сможет самостоятельно включить слой и почитать об ОКН

In [662]:

folium.GeoJson(
    data_pts,
    name="Точечные ОКН",
    zoom_on_click=True,
    marker=folium.Circle(radius=10, color="black", fill_color='green', fill_opacity=0.7, weight=1),
    tooltip=folium.GeoJsonTooltip(fields=["Объект"]),
    popup=folium.GeoJsonPopup(fields=['Объект','дата создания', 'Адрес', 'Категория историко-культурного значения', 'Год постановки ОКН на Госохрану']),
    highlight_function=lambda feature: {
        "fillColor": "yellow"
    },
    show=False,
    popup_keep_highlighted=True,
).add_to(m)

#### 4.4 Добавляем кластеризацию точек
- кластеризуем только точечные ОКН, здания и так хорошо видны

In [663]:
from folium.plugins import MarkerCluster

In [664]:
marker_cluster = MarkerCluster(name='Кластеры точечных ОКН')
mc1= folium.plugins.FeatureGroupSubGroup(marker_cluster, 'Кластеры точечных ОКН')
m.add_child(marker_cluster)
m.add_child(mc1)
mc1.add_child(folium.GeoJson(data_pts.to_json(), embed=False, show=True))


#### 4.5 Добавляем границы Саранска


In [665]:
folium.GeoJson(
    borders,
    name="Границы Саранска",
    style_function=lambda x: {
        "color": 'black',
        "dashArray":"7"
    },
    zoom_on_click=True,
    show=True,
).add_to(m)

- добавляем LayerControl, чтобы включать и выключать слои

In [666]:
folium.LayerControl().add_to(m)
m

#### 4.6 Добавляем плагины


- импортируем плагины


In [667]:
from folium.plugins import MiniMap # мини-карта
from folium.plugins import MeasureControl # измерение расстояний
from folium.plugins import Fullscreen
from folium.plugins import MousePosition

In [668]:
MiniMap(tile_layer="Openstreetmap", position='topright', zoom_level_offset=-4).add_to(m) # мини-карта

m.add_child(MeasureControl(position='topleft')) # измерение расстояний

folium.plugins.Fullscreen(
    position="bottomright",
    title="Expand me",
    title_cancel="Exit me",
    force_separate_button=True,
).add_to(m) # в полный экран

MousePosition(
    position="bottomleft",
    separator=" | ",
    empty_string="NaN",
    lng_first=True,
    num_digits=3,
    prefix="Координаты:"
).add_to(m) # координаты положения мышки

m

## 4. Save map to index.html file and prepare to publish it


In [669]:
m.save("index.html")